In [8]:
import h5py,os,glob
import numpy as np 
import pandas as pd
from astropy.time import Time
import healpy as hp
from healpy.newvisufunc import projview

In [9]:
#fermi grbs
fermi = h5py.File('./fermi_lgrb_skymap.hdf','r')

In [10]:
#swfit grbs
swift = h5py.File('./swift_lgrb_skymap.hdf','r')

In [11]:
swift['o3b'].keys()

<KeysViewHDF5 ['GRB191101A', 'GRB191122A', 'GRB191123A', 'GRB191130A', 'GRB191213A', 'GRB191218A', 'GRB191220A', 'GRB191221B', 'GRB191227A', 'GRB191228A', 'GRB200107B', 'GRB200109A', 'GRB200115A', 'GRB200122A', 'GRB200125A', 'GRB200127A', 'GRB200131A', 'GRB200205B', 'GRB200215A', 'GRB200216B', 'GRB200219A', 'GRB200224A', 'GRB200227A', 'GRB200228B', 'GRB200303A', 'GRB200306A', 'GRB200306C']>

In [12]:
with h5py.File('merge_lgrb.hdf','w') as f:
    for obrun in ['o1','o2','o3a','o3b']:
        fermi_t = []
        swift_t = []
        fermi_name = []
        swift_name = []
        for key in fermi[obrun].keys():
            fermi_t.append(fermi[obrun][key].attrs['gps'])
            fermi_name.append(key)
        for key in swift[obrun].keys():
            swift_t.append(swift[obrun][key].attrs['gps'])
            swift_name.append(key)
        fermi_t = np.array(fermi_t)
        swift_t = np.array(swift_t)
        
        # search for duplicated events with trigger time within [-100,100]
        left = np.searchsorted(fermi_t,  swift_t- 100)
        right = np.searchsorted(fermi_t, swift_t + 100)
        #print(np.max(right - left))
        swift_duplicate = np.where((right - left) > 0)[0]
        fermi_duplicate = left[swift_duplicate]
        print(len(fermi_duplicate))
        #for i in fermi_duplicate:
        #    print(fermi_name[i])
        
        #delete the index of the duplicate events
        fermi_i = np.arange(len(fermi[obrun].keys()))
        nondup_fermi_i = np.delete(fermi_i,fermi_duplicate)
        
        #make a new merged hdf file with non-duplicated events
    
        for i in nondup_fermi_i:
            event_name = list(fermi[obrun].keys())[i]
            f['{}/{}'.format(obrun,event_name)] = fermi[obrun][event_name][:]
            f['{}/{}'.format(obrun,event_name)].attrs['gps'] = fermi[obrun][event_name].attrs['gps']
            f['{}/{}'.format(obrun,event_name)].attrs['satellite'] = 'Fermi'
        for name in swift[obrun].keys():
            f['{}/{}'.format(obrun,name)] = swift[obrun][name][:]
            f['{}/{}'.format(obrun,name)].attrs['gps'] = swift[obrun][name].attrs['gps']
            f['{}/{}'.format(obrun,name)].attrs['satellite'] = 'Swift'

8
15
10
8


In [13]:
swift['o3b'].keys()

<KeysViewHDF5 ['GRB191101A', 'GRB191122A', 'GRB191123A', 'GRB191130A', 'GRB191213A', 'GRB191218A', 'GRB191220A', 'GRB191221B', 'GRB191227A', 'GRB191228A', 'GRB200107B', 'GRB200109A', 'GRB200115A', 'GRB200122A', 'GRB200125A', 'GRB200127A', 'GRB200131A', 'GRB200205B', 'GRB200215A', 'GRB200216B', 'GRB200219A', 'GRB200224A', 'GRB200227A', 'GRB200228B', 'GRB200303A', 'GRB200306A', 'GRB200306C']>

# Check long grbs with LIGO/Virgo paper

In [14]:
# Time(1257495567.572,format='gps',scale='utc').datetime64
f = h5py.File('./merge_lgrb.hdf','r')
name = []
gps = []
satellite = []
obrun = 'o3b'
for key in f[obrun].keys():
    name.append(key)
    gps.append(f[obrun][key].attrs['gps'])
    satellite.append(f[obrun][key].attrs['satellite'])

In [15]:
sort = np.argsort(gps)

In [16]:
for i in sort:
    print(name[i],'//',Time(gps[i],format='gps',scale='utc').datetime64,'//',satellite[i])

GRB191101A // 2019-11-01T21:08:03.350919962 // Swift
GRB191101895 // 2019-11-01T21:28:50.523000002 // Fermi
GRB191108003 // 2019-11-08T00:04:37.595999956 // Fermi
GRB191110587 // 2019-11-10T14:05:34.993000031 // Fermi
GRB191111347 // 2019-11-11T08:19:09.572000027 // Fermi
GRB191111364 // 2019-11-11T08:44:29.947999954 // Fermi
GRB191111547 // 2019-11-11T13:07:10.792000055 // Fermi
GRB191112369 // 2019-11-12T08:51:18.191999912 // Fermi
GRB191113578 // 2019-11-13T13:52:44.522000074 // Fermi
GRB191117006 // 2019-11-17T00:08:28.723999977 // Fermi
GRB191118925 // 2019-11-18T22:12:01.821000099 // Fermi
GRB191119261 // 2019-11-19T06:16:07.174999952 // Fermi
GRB191122A // 2019-11-22T13:32:56.419620037 // Swift
GRB191123A // 2019-11-23T10:38:44.318720102 // Swift
GRB191125206 // 2019-11-25T04:56:43.135999918 // Fermi
GRB191125634 // 2019-11-25T15:12:45.686000109 // Fermi
GRB191129141 // 2019-11-29T03:22:27.127000093 // Fermi
GRB191130253 // 2019-11-30T06:04:41.796999931 // Fermi
GRB191130507 // 

In [17]:
f.close()